In [11]:
import pandas as pd
import ast
df= pd.read_csv('pull_requests_filtered_raw.csv')
df['comments'] = df['comments'].apply(lambda x: ast.literal_eval(x) if isinstance(x, str) else x)
df['review_comments'] = df['comments'].apply(lambda comments: [item for item in comments if item['type'] != 'issue'] if type(comments) is not float else comments)
df = df[df['review_comments'].apply(lambda x: isinstance(x, list) and len(x) > 0)]
df['issue_comments'] = df['comments'].apply(lambda comments: [item for item in comments if item['type'] != 'review'] if type(comments) is not float else comments)
df = df[df['issue_comments'].apply(lambda x: isinstance(x, list) and len(x) > 0)]


import re
def clean_text(text):

    pattern = r"```.*?```|http[s]?://(?:[a-zA-Z]|[0-9]|[$-_@.&+]|[!*\\(\\),]|(?:%[0-9a-fA-F][0-9a-fA-F]))+"
    cleaned_text = re.sub(pattern, "", text, flags=re.DOTALL)

    # Keep only alphanumeric characters and punctuation
    cleaned_text = re.sub(r"[^a-zA-Z0-9.,!?;:'\"(){}\[\]\-]", " ", cleaned_text)

    # Remove extra spaces
    cleaned_text = re.sub(r"\s+", " ", cleaned_text).strip()

    return cleaned_text

def extract_text(comment_thread):
    
    conversation = []
    for comment in comment_thread:
        main_comment = clean_text(comment.get('comment', {}).get('body', ''))
        
        # Extract replies' bodies
        replies = comment.get('replies', [])
        reply_bodies = [reply.get('body', '') for reply in replies]
        
        if main_comment:
            conversation.append(main_comment)

        for r in reply_bodies:
            cleaned_reply = clean_text(r)  # Apply regex cleaning
            if cleaned_reply.strip():  # Ensure we don't add empty strings
                conversation.append(cleaned_reply)
            
    return conversation
# Apply the function to extract text from the comments column
df['processed_comments_review'] = df['review_comments'].apply(extract_text)


df['processed_comments_issue'] = df['issue_comments'].apply(extract_text)

# extract_text(df['review_comments'].iloc[2])


In [24]:
# df['processed_comments_review'] = df['processed_comments_review'].apply(lambda x: ' '.join(x))
df['processed_comments_issue'] = df['processed_comments_issue'].apply(lambda x: ' '.join(x))


In [23]:
df['text_length'] = df['processed_comments_review'].str.len()
print(df['text_length'].describe())


count     3389.000000
mean      1231.977870
std       1331.068074
min          0.000000
25%        267.000000
50%        770.000000
75%       1806.000000
max      11786.000000
Name: text_length, dtype: float64


In [ ]:
from nltk.tokenize import sent_tokenize, word_tokenize
sentences = [sent_tokenize(abstract) for abstract in abstracts]
sentences = [sentence for doc in sentences for sentence in doc]


In [25]:
df['text_length_issue'] = df['processed_comments_issue'].str.len()
print(df['text_length_issue'].describe())

count     3389.000000
mean      1171.753024
std       2289.646158
min          0.000000
25%        130.000000
50%        398.000000
75%       1236.000000
max      65604.000000
Name: text_length_issue, dtype: float64


In [ ]:
long_texts = df[df['processed_comments_review'].str.len() > 3000]


      PR Number  \
97       128248   
126      127503   
157      126971   
205      126461   
286      125773   
293      125709   
328      125422   
450      123830   
471      123578   
494      123245   
495      123205   
497      123169   
530      122752   
540      122639   
686      121488   
716      121262   
717      121257   
720      121132   
736      120878   
751      120748   
804      120225   
866      119341   
938      118452   
1012     117626   
1039     117357   
1102     116737   
1111     116585   
1137     116267   
1138     116260   
1163     115969   
1201     115601   
1204     115522   
1208     115464   
1215     115363   
1237     115128   
1301     114290   
1362     113710   
1363     113679   
1399     113375   
1495     113194   
1497     113156   
1506     113065   
1513     112857   
1516     112806   
1529     112511   
1828     111402   
1883     111212   
1885     111190   
1886     111176   
1893     111151   
1938     110685   
1951     110

In [22]:
len(long_texts['processed_comments_review'].iloc[0])


6297

In [8]:
import pandas as pd
pd.set_option('display.max_colwidth', 255)
pd.set_option('display.max_rows', None)

In [10]:
df = pd.read_csv('bert_topics_review.csv')
df

PR Number  \
0        129755   
1        129675   
2        129299   
3        129232   
4        129088   
5        128984   
6        128947   
7        128942   
8        128919   
9        128909   
10       128870   
11       128856   
12       128794   
13       128789   
14       128547   
15       128455   
16       128452   
17       128432   
18       128430   
19       128365   
20       128308   
21       128259   
22       128248   
23       127935   
24       127883   
25       127862   
26       127798   
27       127765   
28       127743   
29       127731   
30       127728   
31       127726   
32       127715   
33       127503   
34       127444   
35       127362   
36       127277   
37       127274   
38       127248   
39       127022   
40       126989   
41       126971   
42       126820   
43       126798   
44       126755   
45       126622   
46       126606   
47       126584   
48       126556   
49       126461   
50       126438   
51       126435   
52       126412   
53       126408   
54       126402   
55       126389   
56       126368   
57       126350   
58       126256   
59       126245   
60       126210   
61       126158   
62       126155   
63       126145   
64       126081   
65       126046   
66       126020   
67       126013   
68       126004   
69       125943   
70       125918   
71       125917   
72       125897   
73       125892   
74       125880   
75       125869   
76       125799   
77       125773   
78       125765   
79       125753   
80       125716   
81       125711   
82       125709   
83       125708   
84       125690   
85       125689   
86       125664   
87       125663   
88       125642   
89       125631   
90       125629   
91       125627   
92       125625   
93       125619   
94       125553   
95       125527   
96       125520   
97       125503   
98       125492   
99       125490   
100      125489   
101      125474   
102      125457   
103      125422   
104      125403   
105      125383   
106      125349   
107      125331   
108      125327   
109      125326   
110      125309   
111      125243   
112      125231   
113      125200   
114      125109   
115      125101   
116      125054   
117      125032   
118      125006   
119      124992   
120      124961   
121      124934   
122      124886   
123      124863   
124      124797   
125      124751   
126      124732   
127      124723   
128      124720   
129      124677   
130      124660   
131      124562   
132      124557   
133      124545   
134      124528   
135      124513   
136      124506   
137      124470   
138      124448   
139      124418   
140      124410   
141      124373   
142      124357   
143      124337   
144      124312   
145      124261   
146      124202   
147      124187   
148      124176   
149      124159   
150      124106   
151      124017   
152      123953   
153      123900   
154      123860   
155      123846   
156      123842   
157      123830   
158      123758   
159      123753   
160      123665   
161      123658   
162      123633   
163      123621   
164      123578   
165      123565   
166      123493   
167      123491   
168      123489   
169      123434   
170      123428   
171      123356   
172      123341   
173      123311   
174      123306   
175      123254   
176      123248   
177      123245   
178      123205   
179      123199   
180      123169   
181      123144   
182      123057   
183      123045   
184      123032   
185      123031   
186      122963   
187      122796   
188      122759   
189      122752   
190      122748   
191      122705   
192      122650   
193      122648   
194      122639   
195      122598   
196      122595   
197      122590   
198      122589   
199      122562   
200      122554   
201      122526   
202      122522   
203      122518   
204      122514   
205      122477   
206      122473   
207      122462   
208      122460   
209      122453 

In [9]:
df1 = pd.read_csv('bert_topics_review_models.csv')
df1

Topic  Count  \
0       -1    972   
1        0    105   
2        1     95   
3        2     91   
4        3     61   
5        4     46   
6        5     44   
7        6     43   
8        7     42   
9        8     36   
10       9     35   
11      10     34   
12      11     34   
13      12     33   
14      13     32   
15      14     30   
16      15     30   
17      16     29   
18      17     28   
19      18     27   
20      19     27   
21      20     27   
22      21     26   
23      22     26   
24      23     25   
25      24     25   
26      25     24   
27      26     23   
28      27     23   
29      28     23   
30      29     23   
31      30     23   
32      31     21   
33      32     21   
34      33     20   
35      34     20   
36      35     19   
37      36     18   
38      37     18   
39      38     17   
40      39     17   
41      40     17   
42      41     16   
43      42     16   
44      43     16   
45      44     16   
46      45     15   
47      46     15   
48      47     15   
49      48     14   
50      49     14   
51      50     14   
52      51     14   
53      52     14   
54      53     14   
55      54     14   
56      55     14   
57      56     13   
58      57     13   
59      58     13   
60      59     13   
61      60     13   
62      61     13   
63      62     12   
64      63     12   
65      64     12   
66      65     12   
67      66     12   
68      67     12   
69      68     12   
70      69     12   
71      70     12   
72      71     12   
73      72     11   
74      73     11   
75      74     11   
76      75     11   
77      76     11   
78      77     11   
79      78     11   
80      79     11   
81      80     10   
82      81     10   
83      82     10   
84      83     10   
85      84     10   
86      85     10   
87      86     10   
88      87     10   
89      88     10   
90      89     10   
91      90     10   
92      91     10   
93      92     10   
94      93     10   
95      94      9   
96      95      9   
97      96      9   
98      97      9   
99      98      9   
100     99      9   
101    100      9   
102    101      9   
103    102      9   
104    103      8   
105    104      8   
106    105      8   
107    106      8   
108    107      8   
109    108      8   
110    109      8   
111    110      8   
112    111      8   
113    112      8   
114    113      8   
115    114      8   
116    115      8   
117    116      7   
118    117      7   
119    118      7   
120    119      7   
121    120      7   
122    121      7   
123    122      7   
124    123      7   
125    124      7   
126    125      7   
127    126      7   
128    127      7   
129    128      7   
130    129      7   
131    130      7   
132    131      6   
133    132      6   
134    133      6   
135    134      6   
136    135      6   
137    136      6   
138    137      6   
139    138      6   
140    139      6   
141    140      6   
142    141      6   
143    142      6   
144    143      6   
145    144      6   
146    145      6   
147    146      6   
148    147      6   
149    148      5   
150    149      5   
151    150      5   
152    151      5   

                                                                                                                   Name  \
0                                                                                                  -1_use_add_think_don   
1                                                                                             0_climate_mode_hvac_modes   
2                                                                                      1_sneak_tessie_teslemetry_walrus   
3                                                                                            2_username_test_flow_entry   
4                                                                                              3_logger_exist_pr_rebase   
5                               